
## echo TrumpVeryDown.csv| tr -d , |sed -e 's/ /,/g' >> thingPlace


In [1]:
import pickle
from gensim.models.keyedvectors import KeyedVectors

In [2]:
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D, ZeroPadding1D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D, Conv1D, UpSampling1D
from keras.models import Sequential, Model
from keras.optimizers import Adam

import matplotlib.pyplot as plt

import sys

import numpy as np

Using TensorFlow backend.


In [ ]:
from keras.datasets import mnist

In [13]:
from gensim.models import Word2Vec

In [4]:
# import fastText
import numpy as np
from numpy import array
import pandas as pd 

In [41]:
#secondCsv

 For dynamic convert to:

In [5]:

from gensim.models.wrappers import FastText

model = FastText.load_fasttext_format('cc.en.300.bin')


For basic convert back:

In [15]:
modelnow = KeyedVectors.load_word2vec_format('~/MachineLearningBase/cc.en.300.vec')

In [19]:
testtestArray[1][1]

In [ ]:
#fullArray = np.zeros((8850,55,300))

In [13]:
#fullArray = pickle.load( open( "TrumpPostTextSave.p", "rb" ) )

In [14]:
#secondCsv['1',1]

In [40]:
#fullArray2 = fullArray[:][0:51]

In [15]:
fullArray4 = np.zeros((8431,52,300))

In [16]:
# for i in range(0,8431):
#     for j in range(0,52):
#         fullArray4[i][j] = fullMainArray[i][j]

In [17]:
# pickle.dump( fullArray4, open( "TrumpPostFULLFinal.p", "wb" ) )

In [60]:
#len(fullArray3[1][1])

300

In [3]:
fullMainArray = pickle.load( open( "TrumpPostFULLFinal.p", "rb" ) )

In [4]:
fullMainArray.shape

(8431, 52, 300)

In [2]:
#fullMainArray = pickle.load( open( "TrumpPostTextFinalSave.p", "rb" ) )

In [32]:
testArray3 = np.array(["as","they","rounded","a","bend","in","the","path","that","ran","beside","the","river","they","recognized","the","silhouette","of","a","fig","tree","atop","a","nearby","hill","the","weather","was","hot","and","the","days","were","long","the","fig","tree","was","in","full","leaf","but","not","yet","bearing","fruit","soon","they","spotted","other","landmarks","too"])
sampleSentence = np.zeros((1,52,300))
for i in range(0,52):
    sampleSentence[0][i] = modelnow[testArray3[i]]

In [20]:
for i in range(0,52):
    print(fullMainArray[5][i])
    print(modelnow.similar_by_vector(fullMainArray[5][i], topn=1))

In [15]:
# Global Constants
#images_dir = "asdf"
#img_rows = 55 
#img_cols = 300
#noise_len = 100

#images_dir = "asdf"
#img_rows = 55 
#img_cols = 300
#noise_len = 100

In [19]:
# Other Constants
images_dir = "out_place"
img_cols = 52
channels = 300
noise_len = 100

In [20]:
#USE Conv1D

def build_discriminator():
    '''
    Put together a CNN that will return a single confidence output.
    
    returns: the model object
    '''
    img_rows = 300
    img_cols = 52
    img_shape = (img_cols, 300)

    
    model = Sequential()

    model.add(Conv1D(32, kernel_size=5, strides=2, input_shape=img_shape, padding="same"))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.25))
    model.add(Conv1D(64, kernel_size=3, strides=2, padding="same"))
    model.add(ZeroPadding1D(padding=((0,1))))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.25))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Conv1D(128, kernel_size=3, strides=2, padding="same"))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.25))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Conv1D(256, kernel_size=3, strides=1, padding="same"))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dropout(0.25))

    model.add(Flatten())
    model.add(Dense(1, activation='sigmoid'))

    return model

def build_generator():
    '''
    Put together a model that takes in one-dimensional noise and outputs two-dimensional
    data representing a black and white image, with -1 for black and 1 for white.
    
    returns: the model object
    '''

    noise_shape = (noise_len,)
    
    model = Sequential()

    model.add(Dense(img_cols*16*2, activation="relu", input_shape=noise_shape))
    model.add(Reshape((13, 128)))
    model.add(BatchNormalization(momentum=0.8))
    model.add(UpSampling1D(size=2))
    model.add(Conv1D(128, kernel_size=3, padding="same"))
    model.add(Activation("relu"))
    model.add(BatchNormalization(momentum=0.8)) 
    model.add(UpSampling1D(size=2))
    model.add(Conv1D(64, kernel_size=3, padding="same"))
    model.add(Activation("relu"))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Conv1D(300, kernel_size=3, padding="same"))
    model.add(Activation("tanh"))

    return model

def build_combined():
    '''
    Puts together a model that combines the discriminator and generator models.
    
    returns: the generator, discriminator, and combined model objects
    '''
    
    optimizer = Adam(0.0002, 0.5)

    # Build and compile the discriminator
    discriminator = build_discriminator()
    discriminator.compile(loss='binary_crossentropy', 
                          optimizer=optimizer,
                          metrics=['accuracy'])


    # Build and compile the generator
    generator = build_generator()
    generator.compile(loss='binary_crossentropy', optimizer=optimizer)

    # The generator takes noise as input and generates images
    noise = Input(shape=(noise_len,))
    img = generator(noise)
  #  print(len(img))
  #  print(len(img[0]))
  #  print(len(img[0][0]))
    # For the combined model we will only train the generator
    discriminator.trainable = False

    # The discriminator takes generated images as input and determines validity
    valid = discriminator(img)

    # The combined model  (stacked generator and discriminator) takes
    # noise as input => generates images => determines validity 
    combined = Model(inputs=noise, outputs=valid)
    combined.compile(loss='binary_crossentropy', optimizer=optimizer)
    return generator, discriminator, combined

def save_imgs(generator, epoch):
    '''
    Has the generator create images and saves the images in a single file that includes
    the epoch in the filename.
    
    inputs:
        generator: the generator model object returned by build_combined
        epoch: the epoch number (but can be anything that can be represented as a string)
    
    returns: None
    '''
    r, c = 5, 5
    noise = np.random.normal(0, 1, (r * c, noise_len))
   # noise = np.random.normal(0, 1, noise_len).reshape(100,)
    
    gen_img = generator.predict(noise)
    #np.savetxt((str(epoch) + ".csv"), gen_img, delimiter=",")
    pickle.dump( gen_img, open("TTestNowFixedChecking/"+(str(epoch) + ".p"), "wb" ) )
    
#  # Rescale images 0 - 1
#  gen_imgs = 0.5 * gen_imgs + 0.5

#  fig, axs = plt.subplots(r, c)
#  #fig.suptitle("DCGAN: Generated digits", fontsize=12)
#  cnt = 0
#  for i in range(r):
#      for j in range(c):
#          axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
#          axs[i,j].axis('off')
#          cnt += 1
#  fig.savefig(os.path.join(images_dir, 'mnist_{}.png'.format(epoch)))
#  plt.close()

def train(generator, discriminator, combined, epochs, batch_size=128, save_interval=50):
    '''
    Trains all model objects
    
    generator: the generator model object returned by build_combined
    discriminator: the discriminator model object returned by build_combined
    combined: the combined model object returned by build_combined
    epochs: integer, the number of epochs to train for
    batch_size: integer, the number of training samples to use at a time
    save_interval: integer, will generate and save images when the current epoch % save_interval is 0
    
    returns: None
    '''

    # Load the dataset
#   (X_train, _), (_, _) = mnist.load_data()

#   # Rescale -1 to 1
#   X_train = (X_train.astype(np.float32) - 127.5) / 127.5
#   X_train = np.expand_dims(X_train, axis=3)
#   
    X_train = fullMainArray
#  ################################################################################   X_train = sampleSentence
    half_batch = int(batch_size / 2)

    for epoch in range(epochs):

        # ---------------------
        #  Train Discriminator
        # ---------------------

        # Select a random half batch of images
        idx = np.random.randint(0, X_train.shape[0], half_batch)
        imgs = X_train[idx]

        # Sample noise and generate a half batch of new images
        noise = np.random.normal(0, 1, (half_batch, noise_len))
        gen_imgs = generator.predict(noise)

        # Train the discriminator (real classified as ones and generated as zeros)
        d_loss_real = discriminator.train_on_batch(imgs, np.ones((half_batch, 1)))
      #  print(imgs) 
      #  print(np.ones((half_batch, 1)))
      #  print(gen_imgs)
        d_loss_fake = discriminator.train_on_batch(gen_imgs, np.zeros((half_batch, 1)))

        # ---------------------
        #  Train Generator
        # ---------------------

        noise = np.random.normal(0, 1, (batch_size, noise_len))

        # Train the generator (wants discriminator to mistake images as real)
        g_loss = combined.train_on_batch(noise, np.ones((batch_size, 1)))
 
        # If at save interval => save generated image samples and plot progress
        if epoch % save_interval == 0:
            # Plot the progress
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)
            print ("{} [D loss: {}, acc.: {:.2%}] [G loss: {}]".format(epoch, d_loss[0], d_loss[1], g_loss))
            save_imgs(generator, epoch)
            
def show_new_image(generator):
    '''
    Generates and displays a new image
    
    inputs: generator object model returned from build_combined
    
    returns: generated image
    '''
    
    noise = np.random.normal(0, 1, (1, noise_len))
    gen_img = generator.predict(noise)[0][:,:,0]
    
    return plt.imshow(gen_img, cmap='gray', vmin=-1, vmax=1)

In [21]:
#np.random.randint(0, fullArray.shape[0], 64)

In [22]:
# set up directories to hold the images that are saved during training checkpoints.
import os
images_dir = "testOut"
if (not os.path.isdir(images_dir)):
    os.mkdir(images_dir)

In [23]:
generator, discriminator, combined = build_combined()

In [24]:
train(generator, discriminator, combined, epochs=16001, batch_size=32, save_interval=50)

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


0 [D loss: 0.7858262658119202, acc.: 46.88%] [G loss: 0.5346170663833618]
50 [D loss: 0.31934666633605957, acc.: 87.50%] [G loss: 1.3995351791381836]
100 [D loss: 0.1773001253604889, acc.: 96.88%] [G loss: 2.347919464111328]
150 [D loss: 0.08331938087940216, acc.: 100.00%] [G loss: 2.860391139984131]
200 [D loss: 0.026820320636034012, acc.: 100.00%] [G loss: 4.228903293609619]
250 [D loss: 0.034829188138246536, acc.: 100.00%] [G loss: 3.3130245208740234]
300 [D loss: 0.0271848626434803, acc.: 100.00%] [G loss: 4.989794731140137]
350 [D loss: 0.021965142339468002, acc.: 100.00%] [G loss: 5.729642868041992]
400 [D loss: 0.019233690574765205, acc.: 100.00%] [G loss: 6.213037014007568]
450 [D loss: 0.01358093973249197, acc.: 100.00%] [G loss: 5.510708808898926]
500 [D loss: 0.18752802908420563, acc.: 87.50%] [G loss: 12.253978729248047]
550 [D loss: 0.10553161054849625, acc.: 93.75%] [G loss: 9.46042251586914]
600 [D loss: 0.704299807548523, acc.: 71.88%] [G loss: 10.097082138061523]
650 [

5300 [D loss: 0.004357778467237949, acc.: 100.00%] [G loss: 5.754137992858887]
5350 [D loss: 0.08020056784152985, acc.: 96.88%] [G loss: 8.178228378295898]
5400 [D loss: 0.0005455735954456031, acc.: 100.00%] [G loss: 8.328182220458984]
5450 [D loss: 0.026279045268893242, acc.: 100.00%] [G loss: 14.202333450317383]
5500 [D loss: 0.0001842576457420364, acc.: 100.00%] [G loss: 15.625036239624023]
5550 [D loss: 0.0005095184314996004, acc.: 100.00%] [G loss: 16.11809539794922]
5600 [D loss: 0.018684467300772667, acc.: 100.00%] [G loss: 13.516202926635742]
5650 [D loss: 0.006757398601621389, acc.: 100.00%] [G loss: 11.742165565490723]
5700 [D loss: 0.0008001528913155198, acc.: 100.00%] [G loss: 15.652481079101562]
5750 [D loss: 0.0002060342812910676, acc.: 100.00%] [G loss: 8.211267471313477]
5800 [D loss: 0.07490944117307663, acc.: 96.88%] [G loss: 8.340940475463867]
5850 [D loss: 0.00128274061717093, acc.: 100.00%] [G loss: 13.914926528930664]
5900 [D loss: 0.16895705461502075, acc.: 96.88

10400 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10450 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10500 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10550 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10600 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10650 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10700 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10750 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10800 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10850 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10900 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
10950 [D loss: 1.1705525082561508e-07, acc.: 100.00%] [G loss: 16.11809539794922]
11000 [D loss: 1

15450 [D loss: 1.1705525082561508e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15500 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15550 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15600 [D loss: 1.6779862335170037e-06, acc.: 100.00%] [G loss: 16.11809539794922]
15650 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15700 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15750 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15800 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15850 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15900 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.11809539794922]
15950 [D loss: 1.0960467022869125e-07, acc.: 100.00%] [G loss: 16.0822811126709]
16000 [D loss: 3.365603106431081e-06, acc.: 100.00%] [G loss: 16.11809539794922]


In [25]:
# Uncomment to save your model files
generator.save('TTextFullergenerator.h5')
discriminator.save('TTextFullerdiscriminator.h5')
combined.save('TTextFullercombined.h5')

### Success Check:

In [10]:
testing1600now = pickle.load( open( "/Users/cevbain/MachineLearningBase/TTestNowFixedChecking/16000.p", "rb" ) )

In [11]:
testing1600now
for i in range(0,52):
    sampleSentence[0][i] = modelnow[testing1600now[i]]

NameError: name 'modelnow' is not defined

In [16]:
#Control
for i in range(0,52):
    print(modelnow.similar_by_vector(fullMainArray[1][i], topn=1))

[('Heads', 1.0)]
[('of', 1.0)]
[('countries', 0.9999996423721313)]
[('are', 0.9999999403953552)]
[('calling', 0.9999997019767761)]
[('wanting', 0.9999996423721313)]
[('to', 0.9999998211860657)]
[('know', 0.9999998807907104)]
[('why', 1.0)]
[('Senator', 0.9999998807907104)]
[('Schumer', 1.0)]
[('is', 0.9999998807907104)]
[('not', 1.0)]
[('approving', 0.9999997019767761)]
[('their', 0.9999998211860657)]
[('otherwise', 0.9999992847442627)]
[('approved', 0.9999997019767761)]
[('retailersambassador', 0.5213629007339478)]
[('Likewise', 0.9999992847442627)]
[('in', 1.0)]
[('Government', 0.9999994039535522)]
[('lawyers', 0.9999998211860657)]
[('and', 0.9999999403953552)]
[('others', 0.9999997019767761)]
[('are', 0.9999999403953552)]
[('being', 0.9999998807907104)]
[('delayed', 0.9999997615814209)]
[('at', 1.0)]
[('a', 1.0)]
[('record', 0.9999998211860657)]
[('pace.But', 0.44194746017456055)]
[('360', 0.9999999403953552)]
[('great', 0.9999997615814209)]
[('and', 0.9999999403953552)]
[('hardwork

In [15]:
#Check output
for i in range(0,52):
    print(modelnow.similar_by_vector(testing1600now[1][i], topn=1))

[('guysClick', 0.2797005772590637)]
[('Imagine', 0.33793905377388)]
[('BrandsKajariaCeraSomanyNitcoKalinga', 0.3070780336856842)]
[('the', 0.4130028486251831)]
[('the', 0.3828788995742798)]
[('quietly', 0.31263256072998047)]
[('behooves', 0.3410045802593231)]
[('WrightI', 0.3643377125263214)]
[('a', 0.4067404270172119)]
[('a', 0.430534690618515)]
[('That', 0.35388290882110596)]
[('trophyless', 0.33542460203170776)]
[('2K', 0.3236767649650574)]
[('playiing', 0.31074216961860657)]
[('in', 0.36619606614112854)]
[('a', 0.3864564299583435)]
[('a', 0.47258344292640686)]
[('a', 0.49203458428382874)]
[('just', 0.40202292799949646)]
[('just', 0.3766803741455078)]
[('2K', 0.3159021735191345)]
[('gamen', 0.29216092824935913)]
[('1k-', 0.34721314907073975)]
[('a', 0.3937338590621948)]
[('a', 0.4315926432609558)]
[('a', 0.4814150035381317)]
[('a', 0.45654988288879395)]
[('just', 0.3468308448791504)]
[('playiing', 0.32634884119033813)]
[('spend', 0.3464244604110718)]
[('expense.I', 0.352417081594467

---
## Loading Data/Transformation post word seperation code || PRESERVE!

In [3]:
from gensim.models import Word2Vec

In [8]:
firstCsv = pd.read_csv('/Users/cevbain/Documents/TrumpVeryDown.csv')

In [34]:
k = np.zeros((55,300))
for s in range(0,55):
    k[s] = model[secondCsv.iloc[[4],[s]]]

In [72]:
testtestArray = pickle.load( open('TTestChecking/12000.p', "rb" ) )

In [9]:
secondCsv = pd.read_csv('/Users/cevbain/Documents/outFancy3.csv')
secondCsv = pd.read_csv('/Users/cevbain/Documents/outFancy3.csv')

In [10]:
#USED
fullArrayFinal = np.zeros((8431,55,300))
for r in range(0,8431):
    for s in range(0,52):
#         print(secondCsv[str(s)][r])
        try:
            fullArrayFinal[r][s] = model[secondCsv[str(s)][r]]
        except:
            fullArrayFinal[r][s] = np.zeros((300))


pickle.dump(fullArrayFinal, open("TrumpPostFULLSave3.p", "wb" ) ) #The 2 is for safety

HAPPY
NEW
YEAR!
https://t.co/bHoPDPQ7G6
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Heads
of
countries
are
calling
wanting
to
know
why
Senator
Schumer
is
not
approving
their
otherwise
approved
Ambassadors!?
Likewise
in
Government
lawyers
and
others
are
being
delayed
at
a
record
pace!
360
great
and
hardworking
people
are
waiting
for
approval
from....
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
....Senator
Schumer
more
than
a
year
longer
than
any
other
Administration
in
history.
These
are
people
who
have
been
approved
by
committees
and
all
others
yet
Schumer
continues
to
hold
them
back
from
serving
their
Country!
Very
Unfair!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
It’s
incredible
how
Democrats
can
all
use
their
ridiculous
sound
bite
and
say
that
a
Wall
doesn’t
work.
It
does
and
properly
built
almost
100%!
They
say
it’s
old
te

it
should
be
built
is
exceeded
only
by
their
OBSTRUCTION
of
350
great
people
wanting
&amp;
expecting
to
come
into
Government
after
being
delayed
for
more
than
two
years
a
U.S.
record!
nan
nan
nan
nan
nan
nan
The
reason
the
DACA
for
Wall
deal
didn’t
get
done
was
that
a
ridiculous
court
decision
from
the
9th
Circuit
allowed
DACA
to
remain
thereby
setting
up
a
Supteme
Court
case.
After
ruling
Dems
dropped
deal
-
and
that’s
where
we
are
today
Democrat
obstruction
of
the
needed
Wall.
nan
nan
nan
Have
the
Democrats
finally
realized
that
we
desperately
need
Border
Security
and
a
Wall
on
the
Southern
Border.
Need
to
stop
Drugs
Human
TraffickingGang
Members
&amp;
Criminals
from
coming
into
our
Country.
Do
the
Dems
realize
that
most
of
the
people
not
getting
paid
are
Democrats?
nan
nan
nan
nan
nan
nan
Just
returned
from
visiting
our
troops
in
Iraq
and
Germany.
One
thing
is
certain
we
have
incredible
people
representing
our
Country
-
people
that
know
how
to
win!
nan
nan
nan
nan
nan
nan
nan
nan
na

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Will
be
having
lunch
in
White
House
residence
with
large
group
concerning
Border
Security.
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
....going
to
be
there
for
three
months
and
that
was
seven
years
ago
-
we
never
left.
When
I
became
President
ISIS
was
going
wild.
Now
ISIS
is
largely
defeated
and
other
local
countries
including
Turkey
should
be
able
to
easily
take
care
of
whatever
remains.
We’re
coming
home!
nan
nan
nan
I
am
in
the
White
House
working
hard.
News
reports
concerning
the
Shutdown
and
Syria
are
mostly
FAKE.
We
are
negotiating
with
the
Democrats
on
desperately
needed
Border
Security
(Gangs
Drugs
Human
Trafficking
&amp;
more)
but
it
could
be
a
long
stay.
On
Syria
we
were
originally...
nan
nan
nan
nan
nan
OUR
GREAT
COUNTRY
MUST
HAVE
BORDER
SECURITY!
https://t.co/ZGcYygMf3a
nan
nan
nan
nan
nan
nan
nan
nan
nan
na

in
the
Middle
East.”
nan
@IngrahamAngle
nan
So
true
thank
you
Laura!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Col.
Jim
Carafano
on
@IngrahamAngle
“Trump
has
made
the
Middle
East
a
better
place.
When
Trump
came
into
office
ISIS
was
running
amuck
in
the
Middle
East.
Over
a
million
refugees
poured
into
Western
Europe
-
none
of
that
is
happening
today.
That’s
all
due
to
Trump.”
nan
nan
nan
nan
nan
After
historic
victories
against
ISIS
it’s
time
to
bring
our
great
young
people
home!
https://t.co/xoNjFzQFTp
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
....In
any
event
it
goes
on
and
on
&amp;
the
new
AG
who
is
now
being
replaced
by
yet
another
AG
(who
openly
campaigned
on
a
GET
TRUMP
agenda)
does
little
else
but
rant
rave
&amp;
politic
against
me.
Will
never
be
treated
fairly
by
these
people
-
a
total
doub

nan
nan
Required
television
watching
is
last
weeks
@marthamaccallum
interview
with
the
wonderful
wife
of
@RodBlagojevich
and
the
@trishregan
interview
with
a
Jerome
Corsi.
If
that
doesn’t
tell
you
something
about
what
has
been
going
on
in
our
Country
nothing
will.
Very
sad!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
The
Democrats
policy
of
Child
Seperation
on
the
Border
during
the
Obama
Administration
was
far
worse
than
the
way
we
handle
it
now.
Remember
the
2014
picture
of
children
in
cages
-
the
Obama
years.
However
if
you
don’t
separate
FAR
more
people
will
come.
Smugglers
use
the
kids!
nan
nan
nan
Judge
Ken
Starr
former
Solicitor
Generel
&amp;
Independent
Counsel
just
stated
that
after
two
years
“there
is
no
evidence
or
proof
of
collusion”
&amp;
further
that
“there
is
no
evidence
that
there
was
a
campaign
financing
violation
involving
the
President.”
Thank
you
Judge.
@FoxNews
nan
nan
nan
nan
nan
nan
nan
nan
At
the
request
of
many
I
will
be
reviewing
the
case
of
a
“U.S.
Military
he

...

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Just
left
a
great
event
in
Pella.
Going
to
church
tomorrow
in
Muscatine
Iowa.
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
I
will
be
on
FOX
with
the
great
@JudgeJeanine
tonight
at
9pm
EST!
Enjoy!
#Trump2016
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
.@williebosshog
such
an
honor
to
get
your
endorsement.
You
are
a
fantastic
guy!
It
will
not
be
forgotten.
Don
and
Eric
say
hello!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Heading
now
to
Pella
Iowa.
Big
crowd!
Remember
Trump
is
a
big
buyer
of
Pella
windows.
See
you
soon!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


Not
going
to
watch
anymore.
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Low
energy
candidate
@JebBush
has
wasted
$80.00
million
on
his
failed
presidential
campaign.
Millions
spent
on
me.
He
should
go
home
and
relax!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Sad
sack
@JebBush
has
just
done
another
ad
on
me
with
special
interest
money
saying
I
won't
beat
Hillary
-
I
WILL.
But
he
can't
beat
me.
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
So
sad
that
@CNN
and
many
others
refused
to
show
the
massive
crowd
at
the
arena
yesterday
in
Oklahoma.
Dishonest
reporting!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
#MakeAmericaGreatAgain
#Trump2016UNIFYING
THE
NATIONVideo:
https://t.co/1ZWE5R183k
http

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
If
Ted
Cruz
is
so
opposed
to
gay
marriage
why
did
he
accept
money
from
people
who
espouse
gay
marriage?
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Ted
is
the
ultimate
hypocrite.
Says
one
thing
for
money
does
another
for
votes.
https://t.co/hxdfy0mjVw
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Great
new
numbers.
Thank
you!
#MakeAmericaGreatAgain
#Trump2016https://t.co/Z1lQdxQvRL
https://t.co/GFYNUWWCYn
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Ted
Cruz
purposely
and
illegally
did
not
list
on
his
personal
disclosure
form
personally
guaranteed
loans
from
banks.
They
own
him!
nan
nan
nan
nan
nan
n

@kayleighmcenany
is
a
winner!
@donlemon
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Don't
forget
to
watch
The
Tonight
Show
with
the
wonderful
@jimmyfallon
at
11:30
P.M.
You
will
not
be
disappointed!
nan
@NBC
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Face
The
Nation's
interview
of
me
was
the
highest
rated
show
that
they
have
had
in
15
years.
Congratulations
and
WOW!
nan
@CBSNews
@jdickerson
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
.@MajorCBS
Major
Garrett
of
@CBSNews
covers
me
very
inaccurately.
Total
agenda
bad
reporter!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Thank
you
Michael
Harrison
@Talkersmagazine


a
low
energy
stiff
who
should
focus
his
special
interest
money
on
the
many
people
ahead
of
him
in
the
polls.
Has
no
chance!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
.@JebBush
is
a
sad
case.
A
total
embarrassment
to
both
himself
and
his
family
he
just
announced
he
will
continue
to
spend
on
Trump
hit
ads!
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Massive
crowds
expected
in
Mississippi
tomorrow
night.
Look
forward
to
it!
2015
IN
PHOTOS:
https://t.co/29z0XuXVf0
https://t.co/utrl0UnQau
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
#VoteTrump2016
&amp;
together
we
will
#MakeAmericaGreatAgain!
THANK
YOU
for
your
support!
https://t.co/bziqUSHnbi
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan

In [22]:
# Non Functional Bad!!!!
fullArray = np.zeros((8431,55,300))
for r in range(0,8431):
    for s in range(0,52):
        fullArrayFinal[r][s] = modelnow[secondCsv.iloc[[r],[s]]]

----
## Testing The Concept

In [22]:
print(modelnow.similar_by_vector(modelnow["it"], topn=1))

[('it', 0.9999999403953552)]


In [81]:
pickle.dump( fullArray, open( "TrumpPostTextSave.p", "wb" ) )

In [12]:
#  model.predict(testtestArray) #will fail

In [5]:
#model2 = Word2Vec.load('wiki-news-300d-1M.vec')

In [14]:
for i in range(0,52):
    print(modelnow.similar_by_vector(testtestArray[1][i], topn=1))

In [5]:
modelnow.similar_by_vector(np.zeros((300)), topn=1)

[(',', 0.0)]

In [1]:
testArray = "The fancy novel name of book by this guy is built entirely around the fancy phrase and its inventor. It depicts a fictional country off the south area coast that idealizes the pangram, chronicling the effects on literature and social structure as various letters are banned from daily use by government use"

In [2]:
testArray2 = "the","fancy","novel","name","of","book","by","this","guy","is","built","entirely","around","the","fancy","phrase","and","its","inventor","it","depicts","a","fictional","country","off","the","south","area","coast","that","idealizes","the","thing","chronicling","the","effects","on","literature","and","social","structure","as","various","letters","are","banned","from","daily","use","by","government","use"

In [5]:
testArray3 = np.array(["as","they","rounded","a","bend","in","the","path","that","ran","beside","the","river","they","recognized","the","silhouette","of","a","fig","tree","atop","a","nearby","hill","the","weather","was","hot","and","the","days","were","long","the","fig","tree","was","in","full","leaf","but","not","yet","bearing","fruit","soon","they","spotted","other","landmarks","too"])

In [6]:
testArray3 = np.array(["as","they","rounded","a","bend","in","the","path","that","ran","beside","the","river","they","recognized","the","silhouette","of","a","fig","tree","atop","a","nearby","hill","the","weather","was","hot","and","the","days","were","long","the","fig","tree","was","in","full","leaf","but","not","yet","bearing","fruit","soon","they","spotted","other","landmarks","too"])
sampleSentence = np.zeros((1,52,300))
for i in range(0,52):
    sampleSentence[0][i] = modelnow[testArray3[i]]

NameError: name 'modelnow' is not defined

In [18]:
for i in sampleSentence[0]:
    print(modelnow.similar_by_vector(i, topn =1))

In [17]:
for i in testtestArray[1]:
    print(modelnow.similar_by_vector(i, topn =1))

In [16]:
testtestArray[1][1]

In [11]:
for i in testArray3:
    print(modelnow.similar_by_vector(modelnow[i], topn =1))

In [8]:
word_vectors = KeyedVectors.load_fastText_format('cc.en.300.bin', binary=True)
outModel = word2vec.load_fasttext_format()

In [ ]:
#outModel = load_vectors("/Users/cevbain/Downloads/wiki-news-300d-1M.vec")
#modelMain = fasttext.load_model("/Users/cevbain/MachineLearning/cc.en.300.bin")

In [9]:
# outModel.similar_by_vector(new, topn=1, restrict_vocab=None)

In [15]:
model["m"]

-------
## Looking At String Scrubbing

In [56]:
import string

# Thanks to Martijn Pieters for this improved version

# This uses the 3-argument version of str.maketrans
# with arguments (x, y, z) where 'x' and 'y'
# must be equal-length strings and characters in 'x'
# are replaced by characters in 'y'. 'z'
# is a string (string.punctuation here)
# where each character in the string is mapped
# to None
translator = str.maketrans('', '', string.punctuation)

# This is an alternative that creates a dictionary mapping
# of every character from string.punctuation to None (this will
# also work)
#translator = str.maketrans(dict.fromkeys(string.punctuation))

s = 'string with "punctuation" inside of it! Does this work? I hope so.'

# pass the translator to the string's translate method.
print(s.translate(translator))

THisisAthing


In [66]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [75]:
import string

translator2 = str.maketrans('', '', '!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~')

def scrub (stringIn):
    h = stringIn
    try:
        h = h.translate(translator2)
    except:
        return float('nan')
#     h = h.lower()
    return h

In [ ]:
# fullArray = np.zeros((8431,55,300))
for r in range(0,1):
    for s in range(0,55):
    secondCsv[str(s)][5]
        print(modelnow.similar_by_vector(model[secondCsv[str(s)][5]], topn=1))
# secondCsv["0"][5]

In [76]:
# fullArray = np.zeros((8431,55,300))
#for r in range(0,8431):
for s in range(0,55):
    secondCsv[str(s)][5]
    print(modelnow.similar_by_vector(model[secondCsv[str(s)][5]], topn=1))
# secondCsv["0"][5]

[('I’m', 1.0)]
[('in', 1.0)]
[('the', 0.9999999403953552)]
[('Oval', 1.0)]
[('Office', 1.0)]
[('Democrats', 1.0)]
[('come', 1.0)]
[('back', 1.0)]
[('from', 1.0)]
[('vacation', 1.0)]
[('now', 0.9999999403953552)]
[('and', 1.0)]
[('give', 1.0)]
[('us', 1.0)]
[('the', 0.9999999403953552)]
[('votes', 1.0)]
[('necessary', 1.0)]
[('for', 1.0)]
[('Border', 1.0)]
[('Security', 1.0)]
[('including', 0.9999999403953552)]
[('the', 0.9999999403953552)]
[('Wall', 1.0)]
[('You', 1.0)]
[('voted', 1.0)]
[('yes', 1.0)]
[('in', 1.0)]
[('2006', 1.0)]
[('and', 1.0)]
[('3013', 1.0)]
[('One', 0.9999998807907104)]
[('more', 1.0)]
[('yes', 1.0)]
[('but', 1.0)]
[('with', 1.0)]
[('me', 1.0)]
[('in', 1.0)]
[('office', 1.0)]
[('I’ll', 1.0)]
[('get', 1.0000001192092896)]
[('it', 0.9999999403953552)]
[('built', 0.9999999403953552)]
[('and', 1.0)]
[('Fast', 1.0)]


TypeError: 'float' object is not iterable